## Overview:

In this notebook, you will see demo of how [Incremental MV for data lake tables](https://aws.amazon.com/about-aws/whats-new/2023/11/amazon-redshift-incremental-refresh-materialized-views-data-lake-tables-preview/) This feature eliminating the need for full-refreshes of MV which require the re-execution of the underlying select statements and re-writing the data in the materialized view.

We will demonstrate this feature in following three steps.

-  #1 - Create External Iceberg table (Athena)
-  #2 - Insert sample data in Iceberg table (Athena)
-  #2 - Create MV on Iceberg external table (Redshift) 
-  #3 - Browse Data from MV (Redshift)
-  #4 - Add New data to Iceberg tables (Athena) 
-  #5 - Refresh MV and verify new data is available (Redshift)

## Pre-requisites

1. Create Redshift Serverelss workgroup or provisoned cluster in preview mode.  Please refer this [link](https://docs.aws.amazon.com/redshift/latest/mgmt/serverless-workgroup-preview.html) to create preview wokrgroup.

2. Please refer this [link](https://docs.aws.amazon.com/redshift/latest/mgmt/managing-clusters-console.html#cluster-preview) to create provisoned cluster in preview mode.

3. Ensure you setup an IAM role as default IAM role.  Please refer this [link](https://docs.aws.amazon.com/redshift/latest/mgmt/default-iam-role.html#managing-iam-role-console) for instructions.

## create Iceberg test table in Athena
Please refer this [link](https://docs.aws.amazon.com/athena/latest/ug/getting-started.html) to get more details on Athena.

Please refer this [link](https://aws.amazon.com/pm/serv-s3/?gclid=EAIaIQobChMIio7Ri9LRgwMV2mlHAR2_6g9jEAAYASAAEgJDiPD_BwE&trk=fecf68c9-3874-4ae2-a7ed-72b6d19c8034&sc_channel=ps&ef_id=EAIaIQobChMIio7Ri9LRgwMV2mlHAR2_6g9jEAAYASAAEgJDiPD_BwE:G:s&s_kwcid=AL!4422!3!536452728638!e!!g!!aws%20s3!11204620052!112938567994) to get more details on S3

### --Run below scripts to create the iceberg table on Athena

create database iceberg_mv_demo;

create table iceberg_mv_demo.category (
catid int ,
catgroup string ,
catname string ,
catdesc string)
PARTITIONED BY (catid, bucket(16,catid))
LOCATION 's3://<your S3 Bucket>/iceberg/'
TBLPROPERTIES (
'table_type'='iceberg',
'write_compression'='snappy',
'format'='parquet'); 

### -- Run below scripts to insert test data into iceberg table

insert into iceberg_mv_demo.category values
(1, 'Sports', 'MLB', 'Major League Basebal'),
(2, 'Sports', 'NHL', 'National Hockey League'),
(3, 'Sports', 'NFL', 'National Football League'),
(4, 'Sports', 'NBA', 'National Basketball Association'),
(5, 'Sports', 'MLS', 'National Basketball Association');

--Validate data in Category table 

select * from iceberg_mv_demo.category;

## Log in to the Redshift via Query Editor v2 and run the following command

In [0]:
-- Create external table in Redshift

CREATE external schema iceberg_schema
from data catalog
database 'iceberg_mv_demo'
region 'us-east-1'
iam_role default;

-- Query the Iceberg table in Amazon Redshift

SELECT *  FROM "dev"."iceberg_schema"."category";

## Create Materalized view on Iceberg table (Redshift)

In [0]:
-- Create MATERIALIZED view on iceberg table

create MATERIALIZED view mv_category as
select
    *
from
    "dev"."iceberg_schema"."category";

-- verify # rows in  MATERIALIZED view

select count(*) from mv_category; --

# Add new data to Iceberg table (Athena)

Now add data to Iceberg table for Vendor id **11**  through Athena and verify new data is available in Redshift MATERIALIZED view 

-- You ran below SQL in Athena to add data to Iceberg category table  

insert into category values
(12, 'Concerts', 'Comedy', 'All stand-up comedy performances'),
(13, 'Concerts', 'Other', 'General');

## Refresh MV in Redshift

Refresh Materalized view in Redshift and validate data for catids 12 and 13 are now available, and MV gets refreshed incrementally.

### you may need to Refresh MV multiple times due to bug in preview release. Issue is expected to be fixed in GA

In [0]:
Refresh  MATERIALIZED view mv_category;

-- You will get msg - Materialized view mv_category was incrementally updated successfully

select mv_name, status, start_time, end_time
from SYS_MV_REFRESH_HISTORY
where mv_name='mv_category'

--Verify new data is available 
Select count(*) from mv_category; 

select * from mv_category; 

-- you will see catid 12 & 13 along with previous result.

## Cleanup

1. Delete Redshift Serverless workgroup. Please refer this [link](https://docs.aws.amazon.com/redshift/latest/mgmt/serverless_delete-workgroup.html) for documentation to delete workgroup.
2. Delete Redshift Serverelss associated namespace. Please refer this [link](https://docs.aws.amazon.com/redshift/latest/mgmt/serverless-console-namespace-delete.html) for documentation to delete workgroup.